Lambda School Data Science

*Unit 2, Sprint 3, Module 1*

---


# Wrangle ML datasets

- [ ] Continue to clean and explore your data. 
- [ ] For the evaluation metric you chose, what score would you get just by guessing?
- [ ] Can you make a fast, first model that beats guessing?

**We recommend that you use your portfolio project dataset for all assignments this sprint.**

**But if you aren't ready yet, or you want more practice, then use the New York City property sales dataset for today's assignment.** Follow the instructions below, to just keep a subset for the Tribeca neighborhood, and remove outliers or dirty data. [Here's a video walkthrough](https://youtu.be/pPWFw8UtBVg?t=584) you can refer to if you get stuck or want hints!

- Data Source: [NYC OpenData: NYC Citywide Rolling Calendar Sales](https://data.cityofnewyork.us/dataset/NYC-Citywide-Rolling-Calendar-Sales/usep-8jbt)
- Glossary: [NYC Department of Finance: Rolling Sales Data](https://www1.nyc.gov/site/finance/taxes/property-rolling-sales-data.page)

In [50]:
#import file
import pandas as pd
df = pd.read_csv('http://archive.ics.uci.edu/ml/machine-learning-databases/00388/data.csv')
print(df.shape)
df.head()

(11500, 180)


Unnamed: 0   X1   X2   X3   X4   X5  ...  X174  X175  X176  X177  X178  y
0  X21.V1.791  135  190  229  223  192  ...  -103  -127  -116   -83   -51  4
1  X15.V1.924  386  382  356  331  320  ...   157   156   154   143   129  1
2     X8.V1.1  -32  -39  -47  -37  -32  ...   -12   -30   -35   -35   -36  5
3   X16.V1.60 -105 -101  -96  -92  -89  ...   -85   -77   -72   -69   -65  5
4   X20.V1.54   -9  -65  -98 -102  -78  ...   -41   -65   -83   -89   -73  5

[5 rows x 180 columns]

In [0]:
!pip install category_encoders==2.*
!pip install pandas-profiling==2.*

In [51]:
from sklearn.model_selection import train_test_split

train, test = train_test_split(df,train_size=.80,test_size=.2,
                               stratify=df['y'],random_state=7)
train, val = train_test_split(train,train_size=.80,test_size=.2,
                               stratify=train['y'],random_state=7)
train.shape, val.shape, test.shape

((7360, 180), (1840, 180), (2300, 180))

In [0]:
import pandas_profiling
from pandas_profiling import ProfileReport
profile = ProfileReport(train,minimal=True)

profile.to_notebook_iframe()
profile.to_file(output_file='epeleptic_seizure_data_profile.html')

distributed.scheduler - INFO - Clear task state
distributed.scheduler - INFO - Scheduler closing...
distributed.scheduler - INFO - Scheduler closing all comms


###Continue to clean and explore your data.

In [57]:
val['Unnamed: 0'].sample(20)


4819     X14.V1.215
4965      X1.V1.653
7367      X2.V1.634
1639      X2.V1.331
3463       X9.V1.65
1021      X8.V1.374
5297     X15.V1.694
984        X21.V1.4
7896     X19.V1.762
10719    X18.V1.801
10688     X5.V1.814
1687      X5.V1.211
5820     X17.V1.343
10967    X11.V1.812
112      X15.V1.983
2703     X20.V1.661
2060      X21.V1.22
7071       X7.V1.31
10757      X2.V1.75
4485      X12.V1.23
Name: Unnamed: 0, dtype: object

In [0]:
def split_string_X(mystring):
  values = mystring.split('.')
  values = values[0].split('X')
  return values[1]

In [0]:
def split_string_V(mystring):
  values = mystring.split('.')
  values = values[1].split('V')
  return values[1]

In [0]:
def split_string_end(mystring):
  values = mystring.split('.')
  try:
    values[2]
  except:
    return 0
  return values[2]

In [61]:
split_string_end('X10.V1')

0

In [0]:
def wrangle(X):
  X = X.copy()

  # divide "Unamed: 0" into three coulns with the . as the 
  #   seperator
  X['V_id'] = X['Unnamed: 0'].apply(split_string_V)
  X['X_id'] = X['Unnamed: 0'].apply(split_string_X)
  X['data_point'] = X['Unnamed: 0'].apply(split_string_end)
  
  X = X.drop(columns='Unnamed: 0')

  # replace the y with seizure column as the target to
  #  make this a binary classification problem
  X.loc[X['y']==1, 'seizure'] = 1
  X.loc[X['y']!=1, 'seizure'] = 0
  X = X.drop(columns='y')
  
  return X

In [71]:
w_train = wrangle(train)
w_val = wrangle(val)
w_test = wrangle(test)


w_train.shape, w_val.shape, w_test.shape

((7360, 182), (1840, 182), (2300, 182))

In [0]:
target = 'seizure'
features = w_train.drop(columns=target).columns.tolist()

X_train = w_train[features]
y_train = w_train[target]
X_val = w_val[features]
y_val = w_val[target]
X_test = w_test[features]
y_test = w_test[target]

####Featuretools Exploration

In [73]:
sample = w_train[['X1','X2','X3','X4','X5','X6']]
sample.dtypes

X1    int64
X2    int64
X3    int64
X4    int64
X5    int64
X6    int64
dtype: object

In [74]:
import featuretools as ft
import numpy as np

#create an etity set 'es'
es = ft.EntitySet(id='EEG_Seizure_Readings')
# add the dataframe to the entity
es.entity_from_dataframe(entity_id='sample', dataframe=sample, make_index=True,
                         index='sample_index')

Entityset: EEG_Seizure_Readings
  Entities:
    sample [Rows: 7360, Columns: 7]
  Relationships:
    No relationships

In [75]:
# run the deep feature learning to see possible columns
feature_matrix, feature_names = ft.dfs(entityset=es, target_entity='sample',
                       max_depth=2, verbose=1,
                       trans_primitives=['percentile'],#['add', 'multiply', 'divide', 'subtract', 'absolute','percentile'],
                       features_only=False)
feature_matrix.head()

Built 12 features
Elapsed: 00:02 | Remaining: 00:00 | Progress: 100%|██████████| Calculated: 10/10 chunks


X1   X2   X3  ...  PERCENTILE(X4)  PERCENTILE(X5)  PERCENTILE(X6)
sample_index                 ...                                                
0              75   68   55  ...        0.779755        0.786889        0.759579
1            -178 -209 -254  ...        0.029212        0.020992        0.018682
2             587  619  590  ...        0.989198        0.986413        0.981250
3             -83  -88  -90  ...        0.152853        0.146399        0.153804
4            -126 -120  -99  ...        0.152853        0.168886        0.161685

[5 rows x 12 columns]

In [77]:
ft.primitives.list_primitives().tail(40)

name  ...                                        description
22              cum_max  ...  Calculates the max of previous values of an in...
23             multiply  ...  Creates a transform feature that multplies two...
24              weekend  ...  Transform Datetime feature into the boolean of...
25                  add  ...  Creates a transform feature that adds two feat...
26             cum_mean  ...  Calculates the mean of previous values of an i...
27              is_null  ...  For each value of base feature, return 'True' ...
28                 year  ...        Transform a Datetime feature into the year.
29                month  ...       Transform a Datetime feature into the month.
30            longitude  ...  Returns the second value on the tuple base fea...
31                  and  ...  For two boolean values, determine if both valu...
32                 week  ...        Transform a Datetime feature into the week.
33               minute  ...      Transform a Datetime feature into the minute.
34           percentile  ...  For each value of the base feature, determines...
35                 diff  ...  Compute the difference between the value of a ...
36               second  ...      Transform a Datetime feature into the second.
37           days_since  ...  For each value of the base feature, compute th...
38                 hour  ...        Transform a Datetime feature into the hour.
39                  day  ...         Transform a Datetime feature into the day.
40               negate  ...  Creates a transform feature that negates a fea...
41             numwords  ...  Returns the words in a given string by countin...
42              cum_min  ...  Calculates the min of previous values of an in...
43               divide  ...  Creates a transform feature that divides two f...
44  time_since_previous  ...      Compute the time since the previous instance.
45              weekday  ...  Transform Datetime feature into the boolean of...
46            cum_count  ...  Calculates the number of previous values of an...
47             subtract  ...  Creates a transform feature that subtracts two...
48                years  ...  Transform a Timedelta feature into the number ...
49              cum_sum  ...  Calculates the sum of previous values of an in...
50               months  ...  Transform a Timedelta feature into the number ...
51            haversine  ...  Calculate the approximate haversine distance i...
52             absolute  ...                    Absolute value of base feature.
53                   or  ...  For two boolean values, determine if one value...
54                weeks  ...  Transform a Timedelta feature into the number ...
55             latitude  ...  Returns the first value of the tuple base feat...
56              minutes  ...  Transform a Timedelta feature into the number ...
57                  not  ...  For each value of the base feature, negates th...
58              seconds  ...  Transform a Timedelta feature into the number ...
59                hours  ...  Transform a Timedelta feature into the number ...
60                 isin  ...  For each value of the base feature, checks whe...
61                 days  ...  Transform a Timedelta feature into the number ...

[40 rows x 3 columns]

# NYC Data Set Extra Practice

In [0]:
%%capture
import sys

# If you're on Colab:
if 'google.colab' in sys.modules:
    DATA_PATH = 'https://raw.githubusercontent.com/LambdaSchool/DS-Unit-2-Applied-Modeling/master/data/'
    !pip install category_encoders==2.*
    !pip install pandas-profiling==2.*

# If you're working locally:
else:
    DATA_PATH = '../data/'

In [0]:
# Read New York City property sales data
import pandas as pd
df = pd.read_csv(DATA_PATH+'condos/NYC_Citywide_Rolling_Calendar_Sales.csv')

Your code starts here:

In [0]:
# Change column names: replace spaces with underscores


In [0]:
# Get Pandas Profiling Report


In [0]:
# Keep just the subset of data for the Tribeca neighborhood
# Check how many rows you have now. (Should go down from > 20k rows to 146)


In [0]:
# Q. What's the date range of these property sales in Tribeca?


In [0]:
# The Pandas Profiling Report showed that SALE_PRICE was read as strings
# Convert it to integers


In [0]:
# Q. What is the maximum SALE_PRICE in this dataset?


In [0]:
# Look at the row with the max SALE_PRICE


In [0]:
# Get value counts of TOTAL_UNITS
# Q. How many property sales were for multiple units?


In [0]:
# Keep only the single units


In [0]:
# Q. Now what is the max sales price? How many square feet does it have?


In [0]:
# Q. How often did $0 sales occur in this subset of the data?

# There's a glossary here: 
# https://www1.nyc.gov/site/finance/taxes/property-rolling-sales-data.page

# It says:
# A $0 sale indicates that there was a transfer of ownership without a 
# cash consideration. There can be a number of reasons for a $0 sale including 
# transfers of ownership from parents to children. 



In [0]:
# Look at property sales for > 5,000 square feet
# Q. What is the highest square footage you see?


In [0]:
# What are the building class categories?
# How frequently does each occur?


In [0]:
# Keep subset of rows:
# Sale price more than $0, 
# Building class category = Condos - Elevator Apartments

# Check how many rows you have now. (Should be 106 rows.)


In [0]:
# Make a Plotly Express scatter plot of GROSS_SQUARE_FEET vs SALE_PRICE


In [0]:
# Add an OLS (Ordinary Least Squares) trendline,
# to see how the outliers influence the "line of best fit"


In [0]:
# Look at sales for more than $35 million

# All are at 70 Vestry Street
# All but one have the same SALE_PRICE & SALE_DATE
# Was the SALE_PRICE for each? Or in total?
# Is this dirty data?


In [0]:
# Make a judgment call:
# Keep rows where sale price was < $35 million

# Check how many rows you have now. (Should be down to 90 rows.)


In [0]:
# Now that you've removed outliers,
# Look again at a scatter plot with OLS (Ordinary Least Squares) trendline


In [0]:
# Select these columns, then write to a csv file named tribeca.csv. Don't include the index.
